# Interactive Visualization

In this notebook we're going to make an interactive volcano plot. We will add two perpendicular and one horizontal bar in the plot, which will be draggable and which enable the user to color the datapoints according to their position to the bars. To get started with JavaScript we begin with a few simple introduction tasks:

# Configure the import of the d3.js library
The first step is to load the d3 library, which will automatically include all depending libraries required in our code.

In [1]:
%%javascript
require.config({
  paths: {
      //d3: '//cdnjs.cloudflare.com/ajax/libs/d3/3.4.8/d3.min'
      d3: "http://d3js.org/d3.v3.min"
  }
});

<IPython.core.display.Javascript object>

In [3]:
%%javascript
// test if it worked ()
require(["d3"], function(d3) {
  d3.select("body").append("h1").text("Successfully loaded D3 version " + console.log(d3.version));
});

<IPython.core.display.Javascript object>

# Basics
The simplest element to start with is a simple circle. Draw a circle with red fill and black stroke and assign it to the global namespace (window.*)

In [4]:
%%javascript

element.append("<div id='example1'></div>");
require(["d3"], function(d3) {

    //Make an SVG Container
    var svgContainer = d3.select("#example1").append("svg")
                                            .attr("width", 500)
                                            .attr("height", 300);

    //Draw the Circle
    var circle = svgContainer.append("circle")
                             .attr("cx", 400)
                             .attr("cy", 150)
                             .attr("r", 25)
                             .attr("stroke", "black")
                            .style("fill","red");
        
    window.svgContainer = svgContainer
    
    // assign circle to global namespace
    window.circle=circle
});

<IPython.core.display.Javascript object>

Our circle is assigned to a global variable, so we can use it to make the circle blue:

In [5]:
%%javascript

window.circle.attr("r", 25).attr("stroke", "yellow").style("fill","blue");

<IPython.core.display.Javascript object>

## Running JavaScript Code from Python
We are not forced to use %%javascript, but we can also use the python module "IPython.display" e.g. to define a new variable radius = 10.

In [7]:
from IPython.display import Javascript

In [8]:
Javascript("""
           window.radius=10;
           """)

<IPython.core.display.Javascript object>

Switching back to the JavaScript console shows that it worked indeed. We can even use the defined variable to change the radius of our blue circle.

In [9]:
%%javascript
window.circle.attr("r", radius)

<IPython.core.display.Javascript object>

## Binding Data

Drawing each circle individually takes a lot of time, but fortunately there is an option to draw multiple circles at once using arrays:

1. Define the coordinates of the center of 2 circles
```javascript
var data = [{x: 10, y: 10}, {x: 20, y:20}];
```
2. Bind it to your circles and draw it

In [10]:
%%javascript

element.append("<div id='example2'></div>");
require(["d3"], function(d3) {
    
    var data = [{x: 90, y:50}, {x: 200, y: 200}];
    
    //Make an SVG Container
    var svgContainer2 = d3.select("#example2").append("svg")
                                    .attr("width", 500)
                                    .attr("height", 300);
    
    //Draw the Circles
    svgContainer2.selectAll("circle")
                         .data(data)
                         .enter().append("circle")
                         .attr("cx", function(d){return d.x})
                         .attr("cy", function(d){return d.y})
                         .attr("r", 25)
                         .attr("stroke", "black")
                        .style("fill","red");
    
    window.svgContainer2 = svgContainer2
});

<IPython.core.display.Javascript object>

## Convert Data from Pandas to d3.js
To work with d3.js, it's best to format data tables (such those obtained from Pandas) into arrays of Objects.
This is how a JSON example would look like:
```javascript
[
    {column1: value, column2: value, ...}  // row 1
    {column1: value, column2: value, ...}, // row 2
    {column1: value, column2: value, ...}, // row 3
]
```

In [11]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

## Load a data frame in Javascript

It is also possible to load a pandas dataframe into javascript by generating a json object. Dataframe objects already have the method [to_json](http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.to_json.html) which can be used to generate the json object.

### Load your differentially expressed Genes from Day 5/6 from a csv file in a pandas dataframe

In [12]:
fold_change_df = pd.read_csv("results/diff_expr_genes_fold_change.csv")

In [15]:
# calculate the -log10 p values for the plot
fold_change_df_copy = fold_change_df.copy()
fold_change_df_copy['neg_log10_p_value'] = -np.log10(fold_change_df_copy['pvalue'])

In [16]:
df = fold_change_df_copy.rename(columns={'log2 fold change': 'log2_fold_change'})

In [19]:
Javascript("""
           window.fold_change_df={};
           """.format(df.to_json(orient='records')))

<IPython.core.display.Javascript object>

# Create an interactive Vulcano plot with variable pvalue and fold-change cutoffs


In [20]:
%%javascript

// check if the data was loaded successful
element.append("<div id='load data'>" + window.fold_change_df.length + "</div");

<IPython.core.display.Javascript object>

In [21]:
# get min and max of the column log2_fold_change for scaling
df['log2_fold_change'].describe()

count    21834.000000
mean        -0.000461
std          0.029027
min         -0.407640
25%         -0.015148
50%         -0.000668
75%          0.014174
max          0.238675
Name: log2_fold_change, dtype: float64

In [22]:
# get min and max of the column log2_fold_change for scaling
df['neg_log10_p_value'].describe()

count    21834.000000
mean         2.811247
std          2.676361
min          0.301030
25%          0.832325
50%          1.850202
75%          3.918122
max         14.145377
Name: neg_log10_p_value, dtype: float64

In [23]:
%%javascript

element.append("<div id='volcano_plot'></div>");
require(["d3"], function(d3) {
    
// container properties 
var width = 800;
var height = 500;    
var margin = {top: 40, right: 40, bottom: 40, left: 40};
    
//Make an SVG Container
var svgContainer_volcano = d3.select("#volcano_plot").append("svg")
                                .attr("width", width)
                                .attr("height", height);
    
// scale the x coords (=map them from input range to output range)    
var xScale = d3.scale.linear()
                // input range
                .domain([-0.45, 0.25])
                // output range
                .range([0, width - margin.left - margin.right]);

// scale the y coords (=map them from input range to output range)
var yScale = d3.scale.linear()
                // input range
                .domain([0.25, 15])
                // output range
                .range([height - margin.top - margin.bottom, 0]);
    
//Draw the Circles
svgContainer_volcano.selectAll("circle")
                    .data(window.fold_change_df)
                    .enter().append("circle")
                    // scale the x and y coordinates
                    .attr("cx", function(d){return xScale(d.log2_fold_change)})
                    .attr("cy", function(d){return yScale(d.neg_log10_p_value)})
                    // radius = 2
                    .attr("r", 2)
                    .attr("stroke", "black")
                    .style("fill","red");
    
// x axis
var xAxis = d3.svg.axis()
    .scale(xScale)
    .orient("bottom")
    .tickPadding(8);

// y axis
var yAxis = d3.svg.axis()
    .scale(yScale)
    .orient("left")
    .tickPadding(8);
    
// drag event for the horizontal line    
var drag_y = d3.behavior.drag().on('dragstart',function(){
    d3.event.sourceEvent.stopPropagation();
        }).on("drag", function() {       
    
            // get the y coord of the drag event
            var y = d3.event.y
            
            // move the horizontal line by (y-350) 
            d3.select(this).attr("transform","translate(0," + (y-350) + ")");
        
            // update the global variable
            y_height = y
        
            console.log(y_height)
            
            // call recolor function
            recolor_x()
});
    

function recolor_x() {
    
    // get all circles in the container
    var circles = svgContainer_volcano.selectAll("circle")[0]
    
    // iterate over each circle
    for (var i=0; i< circles.length; i++) {    
        
        // if circle is on the right side of the right line or on the left side of the left line
        if ((circles[i].getAttribute('cx') > x_axis_right) || (circles[i].getAttribute('cx') < x_axis_left)){
            
            // if circle is above the horizontal line
            if(circles[i].getAttribute('cy') < y_height) {
                
                // redraw the circle with blue color
                circles[i].setAttribute("style", "fill: blue;")
                
            } else {
                
                // redraw the circle with red color
                circles[i].setAttribute("style", "fill: red;")
            }

        } else {
            
            // redraw the circle with red color
            circles[i].setAttribute("style", "fill: red;")
            
        }
    }
}  

// default variables for the position of the three lines    
var x_axis_right = 0
var x_axis_left = 0
var y_height = 350
    
// drag events for the perpendicular lines    
var drag = d3.behavior.drag().on('dragstart',function(){
      d3.event.sourceEvent.stopPropagation();})
            .on("drag", function() {       
                
                // get the x coord of the drag event
                var x = d3.event.x
    
                // move the left line by (x-425) 
                d3.select(this).select('#left').attr("transform","translate(" + (x-425) + ",0)");
                
                // move the right line by (x+425) 
                d3.select(this).select('#right').attr("transform","translate(" + (-x+425) + ",0)")
                
                // update the global variable
                x_axis_left = x;
                x_axis_right = -x+925
                
                // call recolor function
                recolor_x();
    });
    
// coordinates for the horizontal line    
var line_coords_horizontally = [{x1: 5, y1: 350, x2: width, y2: 350, id: 'horizontal'}]
    
// create the horizontal line && draw it
var line_hor = svgContainer_volcano.selectAll("line")
                         .data(line_coords_horizontally)
                          .enter().append("line")
                          .attr("x1", function(d){return d.x1})
                          .attr("y1", function(d){return d.y1})
                         .attr("x2", function(d){return d.x2})
                         .attr("y2", function(d){return d.y2})
                        .attr("id", function(d) { return d.id})
                          .attr("stroke", "black")
                          .attr("stroke-width", 4)
                        .call(drag_y);
    
// create a group to move the two perpendicular lines at the same time
var group = svgContainer_volcano.append("g")
  
// coordinates for the perpendicular line
var line_coords = [
  {x1: 425, y1: 0, x2: 425, y2: height, id: 'left'},
  {x1: 500, y1: 0, x2: 500, y2: height, id: 'right'}
];

// create the perpendicular lines and draw them    
var lines = group.selectAll("line")
                         .data(line_coords)
                          .enter().append("line")
                          .attr("x1", function(d){return d.x1})
                          .attr("y1", function(d){return d.y1})
                         .attr("x2", function(d){return d.x2})
                         .attr("y2", function(d){return d.y2})
                        .attr("id", function(d) { return d.id})
                          .attr("stroke", "black")
                          .attr("stroke-width", 4);

// drag function for the group container
group.call(drag);
    
// draw the x axis    
svgContainer_volcano.append("g")
    .attr("class", "x axis")
    .attr("transform", "translate(0," + height*0.9 + ")")
    .call(xAxis);

// draw the y axis
svgContainer_volcano.append("g")
    .attr("class", "y axis")
    .attr("transform", "translate(" + margin.left +", 0)")
    .call(yAxis);

// make variables global 
window.svgContainer_volcano = svgContainer_volcano
window.group = group


});

<IPython.core.display.Javascript object>